# Goal:
- Pull NASA LANCE Ultra Real Time (URT) Data via API call
- Preprocess and clean data
- Display fire perimeter on a map

API Resource Page: https://firms.modaps.eosdis.nasa.gov/api/area/html  
API Map Key: a17758d8f727c27ac9659247ed9ba826

Notes:
- Fire & Thermal Hotspots with REST API
- not the most consistent data pulls
- Sometimes a lot of data is shown, other times states "Error in processing: No data"
- requires email for a 'Map Key'
- 5000 credits, refreshes every 10 mins

In [1]:
import folium
from folium import plugins
import requests
import pandas as pd
from io import StringIO
from datetime import date

map_key = "a17758d8f727c27ac9659247ed9ba826"
usa_bbox = "-125,24,-66,50"
day_range = 1 # range of data from 1-5 days
date = str(date.today())

# satellites
satellites = ["VIIRS_NOAA21_NRT", "LANDSAT_NRT", "MODIS_NRT"]
essential_cols = ['latitude', 'longitude', 'acq_date', 'acq_time', 'confidence', 'satellite']

# main dataframe
df_list = []

# returns in CSV format
for satellite in satellites:
    url = f"https://firms.modaps.eosdis.nasa.gov/api/area/csv/{map_key}/{satellite}/{usa_bbox}/{day_range}/{date}"
    response = requests.get(url)
    print("API call success")
    
    if response.status_code == 200:
        # turn csv into dataframe
        csv_text = response.text.strip()
        csv_file_object = StringIO(csv_text)
        satellite_df = pd.read_csv(csv_file_object, sep=',')

        # track which satellite responsible
        satellite_df['satellite'] = satellite
        
        # append to df_list 
        df_list.append(satellite_df[essential_cols])
        
    else:
        print(f"Status Code: {response.status_code}")

# concatinate all satellite dataframes into one dataframe
if df_list:
    df = pd.concat(df_list, ignore_index=True)

API call success
API call success
API call success


In [2]:
df

latitude  longitude    acq_date  acq_time confidence         satellite
0     34.74667  -77.96172  2026-03-01       658          n  VIIRS_NOAA21_NRT
1     34.83886  -79.74046  2026-03-01       658          n  VIIRS_NOAA21_NRT
2     35.08345  -77.91115  2026-03-01       658          n  VIIRS_NOAA21_NRT
3     35.10405  -78.00142  2026-03-01       658          n  VIIRS_NOAA21_NRT
4     35.17427  -80.22610  2026-03-01       658          n  VIIRS_NOAA21_NRT
...        ...        ...         ...       ...        ...               ...
4026  42.80846  -96.76495  2026-03-01      2105         59         MODIS_NRT
4027  38.01400 -121.86849  2026-03-01      2241         87         MODIS_NRT
4028  38.01618 -121.85586  2026-03-01      2241         57         MODIS_NRT
4029  38.49487 -121.93523  2026-03-01      2241         75         MODIS_NRT
4030  48.33033 -122.61667  2026-03-01      2244         52         MODIS_NRT

[4031 rows x 6 columns]

In [3]:
# separate data into two dataframes
df_coords = df.loc[:, ("latitude", "longitude")]
df_metadata = df[["acq_date", "acq_time", "satellite"]]

In [4]:
# initialize the map
m = folium.Map([40.0, -96.0], zoom_start=4, tiles="Cartodb dark_matter")

# layer for satellite hotspots
fire_hotspot_layer = folium.FeatureGroup(name='fire_hotspot_layer').add_to(m)

In [5]:
# create a list of dictionaries for the metadata
metadata_list = df_metadata.to_dict('records')

# zip the coordinates and metadata together for the loop
for coord, meta in zip(df_coords.values, metadata_list):
    x, y = coord[0], coord[1]
    
    # Create a nice string for the popup
    # Use <br> for line breaks in HTML
    html_popup = f"""
    <b>Satellite:</b> {meta['satellite']}<br>
    <b>Date:</b> {meta['acq_date']}<br>
    <b>Time:</b> {meta['acq_time']}
    """
    folium.CircleMarker(
        location=[x, y],
        # Tooltip shows on hover, Popup shows on click
        popup=folium.Popup(html_popup, max_width=200),
        tooltip="Click for Metadata",
        radius=1,
        color='red',
        fill=True,
        fill_color='red',
        fill_opacity=0.7
    ).add_to(fire_hotspot_layer)
    
    # folium.Marker(
    #     location=[x, y],
    #     # Tooltip shows on hover, Popup shows on click
    #     popup=folium.Popup(html_popup, max_width=200),
    #     tooltip="Click for Metadata",
    #     icon=folium.Icon(color="red", icon="fire", prefix="fa"),
    # ).add_to(fire_hotspot_layer)

In [6]:
m